In [1]:
"""
!pip install convokit
!pip install transformers[torch]
!pip install accelerate
# !pip install transformers_interpret
!pip install git+https://github.com/allenai/longformer.git
!pip install jsonlines
!pip install shap
!pip install openai==1.12.0     # Azure AI
!pip install openai==0.28       # OPENAI API
"""

'\n!pip install convokit\n!pip install transformers[torch]\n!pip install accelerate\n# !pip install transformers_interpret\n!pip install git+https://github.com/allenai/longformer.git\n!pip install jsonlines\n!pip install shap\n!pip install openai==1.12.0     # Azure AI\n!pip install openai==0.28       # OPENAI API\n'

In [2]:
import os
import matplotlib.pyplot as plt
import numpy as np
import re
import matplotlib.pyplot as plt
from sklearn.datasets import fetch_openml
import time
from sklearn import tree
import pandas as pd
import jsonlines
from datetime import date
import csv
import openai
openai.api_key = "XXXXXXXXXXXXXXXXXXX"
import json
import random
import torch
from torch.nn import L1Loss
from sklearn.metrics import mean_absolute_error
import numpy as np
from sklearn.metrics import mean_squared_error
from scipy import stats

import convokit
import spacy
from convokit import Corpus, Speaker, Utterance
from convokit import download
from convokit import TextParser

# 0. Load Data Function

## 0.1. OUM data

In [ ]:
# Load the data
def load_data_oum(label='after'):
    final_convs = []
    final_labels = []
    wizards_data = []
    moral_foundations = ["care", "fairness", "liberty", "loyalty", "authority", "sanctity", "none"]
    input_files = {"wizards": "../wizards_dialogues.json", "final_argubot": "../argubot_final_exp.json",
                   "models_dialogues": "../models_dialogues.json"}
    dials_with_scores = {"wizards": {}, "final_argubot": {}, "models_dialogues": {}}


    for key in input_files:
        input_file = input_files[key]
        with open(input_file, "r", encoding="utf-8") as f:
            data = json.load(f)
        for d in data:
            is_wiki = False
            for m in d["messages"]:
                if 'model' in m and (m['model'] == 'wikibot' or m['model'] == 'controlbot'):
                    is_wiki = True
                    break
            if is_wiki:
                continue
            yes_no = 'none'
            k = 'Did you vote for (Leave) or against (Remain) Brexit in the 2016 UK referendum?'
            if k in d['participant_info']:
                if d['participant_info'][k].lower() == 'against (remain)':
                    yes_no = 'no'
                elif d['participant_info'][k].lower() == 'for (leave)':
                    yes_no = 'yes'
                else:
                    yes_no = 'none'

            k = 'In the referendum on whether the UK should remain a member of the EU (BREXIT), how did you vote?'
            if k in d['participant_info']:
                if d['participant_info'][k].lower() == 'remain (against brexit)':
                    yes_no = 'no'
                elif d['participant_info'][k].lower() == 'leave (for brexit)':
                    yes_no = 'yes'
                else:
                    yes_no = 'none'
            k = 'Have you had at least one dose of an approved Covid-19 vaccine?'
            if k in d['participant_info']:
                if d['participant_info'][k].lower() == 'yes':
                    yes_no = 'yes'
                elif d['participant_info'][k].lower() == 'no':
                    yes_no = 'no'
            k = 'Are you a vegan?'
            if k in d['participant_info']:
                if d['participant_info'][k].lower() == 'yes':
                    yes_no = 'yes'
                elif d['participant_info'][k].lower() == 'no':
                    yes_no = 'no'

            if yes_no == 'none':
                continue

            if 'Questions' in d['participant_info']:
                for q in d['participant_info']['Questions']:
                    if "final" in input_file:
                        if label == 'oum':
                            continue
                        if d['participant_info']['Questions'][q]['after'] == -1:
                            continue
                    elif d['participant_info']['Questions'][q]['before'] == -1 or d['participant_info']['Questions'][q]['after'] == -1:
                        continue
                    if 'good reasons' in q.lower():
                        if d['topic'] != 'brexit' and 'not' in q.lower() and yes_no == 'no':
                            continue
                        if d['topic'] != 'brexit' and 'not' not in q.lower() and yes_no == 'yes':
                            continue
                        if 'leave' in q.lower() and yes_no == 'yes':
                            continue
                        if 'remain' in q.lower() and yes_no == 'no':
                            continue
                        if d["_id"] not in dials_with_scores[key]:
                            text = ''
                            dials_with_scores[key][d["_id"]] = {"topic": d["topic"], "dataset": key}
                            for message in d['messages']:
                                if message['role'] == 'admin' or 'modified_argument' not in message:
                                    continue

                                text = text + '\n\n' + '<' + message['role'] + '>' + '\n' + message['modified_argument']
                            dials_with_scores[key][d["_id"]]['text'] = text.strip()
                            final_convs.append(text.strip())

                    if 'good reasons' in q.lower():
                        if False and label == 'oum': 
                            final_labels.append(float(d['participant_info']['Questions'][q]['after']) - float(d['participant_info']['Questions'][q]['before']))
                        else:
                            final_labels.append(float(d['participant_info']['Questions'][q]['after']))
                        oum = d['participant_info']['Questions'][q]['after'] - d['participant_info']['Questions'][q]['before'] if "final" not in input_file else None
                        dials_with_scores[key][d["_id"]]["good_reasons"] = {"oum": oum, "after": d['participant_info']['Questions'][q]['after']}
                        if 'before' in d['participant_info']['Questions'][q] and d['participant_info']['Questions'][q]['before'] != -1:
                            dials_with_scores[key][d["_id"]]["good_reasons"]['before'] = d['participant_info']['Questions'][q]['before']
                        else:
                            dials_with_scores[key][d["_id"]]["good_reasons"]['before'] = None

    assert len(final_convs) == len(final_labels)
    return final_convs, final_labels



def get_utterances(text):
    # Splitting the input text into lines
    lines = text.split('\n')
    # Variable to keep the cleaned lines
    cleaned_lines = []
    # Variable to keep track of whether the next line should be added
    add_next_line = False
    speakers = []
    for line in lines:
        # If the line is a participant tag, set the flag to add the next line
        if line.strip() == '<participant>':
            add_next_line = True
            speaker = 'participant'
        elif line.strip() in ['<woz>', '<chatbot>']:
            add_next_line = True
            speaker = 'non-participant'
        elif add_next_line:
            # If the flag is set, add this line to the cleaned list and reset the flag
            cleaned_lines.append(line)
            add_next_line = False
            speakers.append(speaker)
    # Join the cleaned lines back into a single string
    cleaned_text = '\n\n'.join(cleaned_lines)
    return cleaned_text, speakers

### Bot/Woz's data
conversations, labels = load_data_oum(label='after')
utterances, speakers = [get_utterances(c)[0] for c in conversations], [get_utterances(c)[1] for c in conversations]

## 0.2. Wikitactics

In [ ]:
import json
import pandas as pd
import numpy as np
from collections import Counter

def load_data_wikitac():
    with open('../wikitactics.json') as f:
        data = json.load(f)

    conversations = []
    utterances_cleaned = []
    labels = []

    for dispute in data:
        users = list()
        conversation = ''
        utt_cleaned = ''
        for utterance in dispute['utterances']:
            username = utterance['username']
            text = utterance['text']
            conversation += f"<user_id={username}>\n{text}\n\n"
            utt_cleaned += text + '\n\n'
        conversations.append(conversation)
        utterances_cleaned.append(utt_cleaned)
        labels.append(dispute['escalation_label'])

    return conversations, utterances_cleaned, labels

conversations, utterances, labels = load_data_wikitac()

## 0.3. Articles for Deletion (AFD)

In [ ]:
def load_data_afd():
    # Load the data from the JSON file
    with open('../afd_1000_randomised_dialogues.json', 'r') as json_file:
        data_dict = json.load(json_file)

    # Extract the conversations, utterances, and labels from the data dictionary
    conversations = data_dict['conversations']
    utterances = data_dict['utterances']
    labels = data_dict['labels']

    return conversations, utterances, labels

conversations, utterances, labels = load_data_afd()

# 3. Disagreement Labels and Non-Disagreement Labels

## 3.1. Prompt GPT-4 to annotate the features - OUM Data

In [4]:
utterance = "THIS IS AN UTTERANCE."

ini = """Below are two sets of linguistic features for disagreement levels and non-disagreement labels."""

disagreement_levels = """\n\n
Disagreement Levels:

Level 0: Name calling/hostility - Direct insults, or use of an equally hostile tone or language.

Level 1: Ad hominem/ad argument - An attack to the person, often used to attempt to discredit an opponent (e.g., "I know better than you; you do not have a physics degree"). This category was extended to include "ad argument", where someone insults another's argument (e.g., "that is ridiculous") without responding to its content.

Level 2: Attempted derailing/off-topic - This category was added to address comments which are unrelated to the current line of discussion and fail to further the argument, while still being argumentative. This category is also represented in the Talk page taxonomy of Viegas et al. (2007). It was assigned a lower level as it can be detrimental to the argument, by taking focus away from the main topic.

Level 3: Policing the discussion - Graham (2008) referred to this as "responding to tone" with the description "responses to the writing, rather than the writer. The lowest form of these is to disagree with the author’s tone". By expanding the definition to "policing the discussion", the idea is to include people saying "You’ve said that before", telling people to "calm down", correcting spelling errors, or citing discussion policy (i.e. "no personal attacks"). It ignores the argument’s content.

Level 4: Stating your stance - Graham (2008) referred to this as "contradiction", with the description "to state the opposing case, with little or no supporting evidence".

Level 4: Repeated argument - Level added to describe re-stating an argument used before, potentially using different words. This level was chosen as, similar to Level 4: Stating your stance, it does engage with the argument but does not further the discussion.

Level 5: Counterargument - Described as "contradiction plus new reasoning and/or evidence", which does not directly address the opponent’s argument.

Level 6: Refutation - Directly responding to the argument and explaining why it is mistaken, using new evidence or reasoning.

Level 7: Refuting the central point - Graham (2008) notes that "Truly refuting something requires one to refute its central point, or at least one of them." Unfortunately, the central point can be quite subjective and difficult to recognize for non-experts, and may change throughout a conversation. As such, we use this category as a prime example of a “good” refutation, which is of course still subjective and may be rolled up into Level 6.
"""


non_disagreement_labels = """\n\n
Non-Disagreement Labels:

Label A: Bailing out - An indication that a person is giving up on a conversation and will no longer engage.

Label B: Contextualisation - In the first utterance, a person "sets the stage" by describing which aspect of the discussion they are challenging. This does not directly disagree with anyone, and is therefore a non-disagreement move.

Label C: Asking questions - Seeking to understand another person’s opinion better. This does not include rhetorical questions, which are generally disagreement moves.

Label D: Providing clarification - Answering questions or providing information which seeks to create understanding, rather than only furthering a point.

Label E: Suggesting a compromise - An attempt to find a midway between one’s own point and the opposer’s.

Label F: Coordinating - For example, Wikipedia Talk pages are primarily used to for goal-oriented discussions, to coordinate edits to a page. As part of disagreement threads, there is often also some discussion of these edits. This can signal that a compromise has been found.

Label G: Conceding / recanting - An explicit admission that an interlocutor is willing to relinquish their point.

Label H: I don't know - Admitting that one is uncertain. This signals that an person is receptive to the idea that there are unknowns which may impact their argument.

Label I: Other - For utterances not covered by any other class, for instance, social niceties.
"""


final = """\n\n
Given a conversation history (which can be empty if the new utterance is the first utterance made in the conversation), please analyze a new utterance from an individual in a conversation about a controversial topic:

*CONVERSATION HISTORY*: "{conv_history}"

*NEW UTTERANCE*: "{utterance}"

Noteworthy, the conversation history is provided for you to simply understand the utterances made before the new utterance so as to help you better annotate the new utterance.

Thus, please do not annotate the entire conversation but annotate only the new utterance by determining its appropriate disagreement level and/or non-disagreement label(s). Please provide the final answer directly with no reasoning steps.

If the new utterance fits multiple categories, list all that apply. Ensure that your final answer clearly identifies whether each of the disagreement levels (0-7) and non-disagreement labels (A-I) are applicable (1) or not applicable (0) to the new utterance.

For clarity, your response should succinctly be presented in a structured list format, indicating the presence (1) or absence (0) of each level and label as follows:

- Level 0: [1/0]
- Level 1: [1/0]
- Level 2: [1/0]
- Level 3: [1/0]
- Level 4: [1/0]
- Level 5: [1/0]
- Level 6: [1/0]
- Level 7: [1/0]
- Label A: [1/0]
- Label B: [1/0]
- Label C: [1/0]
- Label D: [1/0]
- Label E: [1/0]
- Label F: [1/0]
- Label G: [1/0]
- Label H: [1/0]
- Label I: [1/0]
"""

prompt = ini + disagreement_levels + non_disagreement_labels + final

formatted_prompt = prompt.format(utterance=utterance, conv_history='')
print(formatted_prompt)

Given the following two sets of textual features for disagreement levels and non-disagreement labels:


Disagreement Levels:

Level 0: Name calling/hostility - Direct insults, or use of an equally hostile tone or language.

Level 1: Ad hominem/ad argument - An attack to the person, often used to attempt to discredit an opponent (e.g., "I know better than you; you do not have a physics degree"). This category was extended to include "ad argument", where someone insults another's argument (e.g., "that is ridiculous") without responding to its content.

Level 2: Attempted derailing/off-topic - This category was added to address comments which are unrelated to the current line of discussion and fail to further the argument, while still being argumentative. This category is also represented in the Talk page taxonomy of Viegas et al. (2007). It was assigned a lower level as it can be detrimental to the argument, by taking focus away from the main topic.

Level 3: Policing the discussion - Gr

## 3.2. Prompt GPT-4 to annotate the features - AFD Data

In [ ]:
utterance = "THIS IS AN UTTERANCE"

ini = """Below are two sets of linguistic features for disagreement levels and non-disagreement labels."""

disagreement_levels = """\n\n
Disagreement Levels:

Level 0: Name calling/hostility - Direct insults, or use of an equally hostile tone or language.

Level 1: Ad hominem/ad argument - An attack to the person, often used to attempt to discredit an opponent (e.g., "I know better than you; you do not have a physics degree"). This category was extended to include "ad argument", where someone insults another's argument (e.g., "that is ridiculous") without responding to its content.

Level 2: Attempted derailing/off-topic - This category was added to address comments which are unrelated to the current line of discussion and fail to further the argument, while still being argumentative. This category is also represented in the Talk page taxonomy of Viegas et al. (2007). It was assigned a lower level as it can be detrimental to the argument, by taking focus away from the main topic.

Level 3: Policing the discussion - Graham (2008) referred to this as "responding to tone" with the description "responses to the writing, rather than the writer. The lowest form of these is to disagree with the author’s tone". By expanding the definition to "policing the discussion", the idea is to include people saying "You’ve said that before", telling people to "calm down", correcting spelling errors, or citing discussion policy (i.e. "no personal attacks"). It ignores the argument’s content.

Level 4: Stating your stance - Graham (2008) referred to this as "contradiction", with the description "to state the opposing case, with little or no supporting evidence".

Level 4: Repeated argument - Level added to describe re-stating an argument used before, potentially using different words. This level was chosen as, similar to Level 4: Stating your stance, it does engage with the argument but does not further the discussion.

Level 5: Counterargument - Described as "contradiction plus new reasoning and/or evidence", which does not directly address the opponent’s argument.

Level 6: Refutation - Directly responding to the argument and explaining why it is mistaken, using new evidence or reasoning.

Level 7: Refuting the central point - Graham (2008) notes that "Truly refuting something requires one to refute its central point, or at least one of them." Unfortunately, the central point can be quite subjective and difficult to recognize for non-experts, and may change throughout a conversation. As such, we use this category as a prime example of a “good” refutation, which is of course still subjective and may be rolled up into Level 6.
"""


non_disagreement_labels = """\n\n
Non-Disagreement Labels:

Label A: Bailing out - An indication that a person is giving up on a conversation and will no longer engage.

Label B: Contextualisation - In the first utterance, a person "sets the stage" by describing which aspect of the discussion they are challenging. This does not directly disagree with anyone, and is therefore a non-disagreement move.

Label C: Asking questions - Seeking to understand another person’s opinion better. This does not include rhetorical questions, which are generally disagreement moves.

Label D: Providing clarification - Answering questions or providing information which seeks to create understanding, rather than only furthering a point.

Label E: Suggesting a compromise - An attempt to find a midway between one’s own point and the opposer’s.

Label F: Coordinating - For example, Wikipedia Talk pages are primarily used to for goal-oriented discussions, to coordinate edits to a page. As part of disagreement threads, there is often also some discussion of these edits. This can signal that a compromise has been found.

Label G: Conceding / recanting - An explicit admission that an interlocutor is willing to relinquish their point.

Label H: I don't know - Admitting that one is uncertain. This signals that an person is receptive to the idea that there are unknowns which may impact their argument.

Label I: Other - For utterances not covered by any other class, for instance, social niceties.
"""


final = """\n\n
Given a conversation history (which can be empty if the new utterance is the first utterance made in the conversation), please analyze a new utterance from an individual (identified by a unique user_id) in a conversation discussing with others about a potentially controversial article that perhaps should be deleted from Wikipedia Talk pages:

*CONVERSATION HISTORY*: "{conv_history}"

*NEW UTTERANCE*: "{utterance}"

Noteworthy, the conversation history is provided for you to simply understand the utterances made before the new utterance so as to help you better annotate the new utterance.

Thus, please do not annotate the entire conversation but annotate only the new utterance by determining its appropriate disagreement level and/or non-disagreement label(s). Please provide the final answer directly with no reasoning steps.

If the new utterance fits multiple categories, list all that apply. Ensure that your final answer clearly identifies whether each of the disagreement levels (0-7) and non-disagreement labels (A-I) are applicable (1) or not applicable (0) to the new utterance.

For clarity, your response should succinctly be presented in a structured list format, indicating the presence (1) or absence (0) of each level and label as follows:

- Level 0: [1/0]
- Level 1: [1/0]
- Level 2: [1/0]
- Level 3: [1/0]
- Level 4: [1/0]
- Level 5: [1/0]
- Level 6: [1/0]
- Level 7: [1/0]
- Label A: [1/0]
- Label B: [1/0]
- Label C: [1/0]
- Label D: [1/0]
- Label E: [1/0]
- Label F: [1/0]
- Label G: [1/0]
- Label H: [1/0]
- Label I: [1/0]
"""

prompt = ini + disagreement_levels + non_disagreement_labels + final

formatted_prompt = prompt.format(utterance=utterance, conv_history='')
print(formatted_prompt)

## 3.3. Prompt GPT-4 to annotate the features - Wikitactics

In [5]:
# Same prompt template as OUM and AFD but modifying slightly the prompt (see Table 12 of the paper).

## 3.4 Run GPT-4

In [18]:
import collections
import time
import os
import openai
import os

import json

def extract_and_remove_last_word(string):
    # Split the string into lines
    lines = string.splitlines(keepends=True)

    # Extract the last word from the last line
    last_line = lines[-1]
    words = last_line.split()
    last_word = words[-1]

    # Remove the last word from the last line
    lines[-1] = ' '.join(words[:-1]) + ('\n' if last_line.endswith('\n') else '')

    # Join the lines back into a string
    string_without_last_word = ''.join(lines)

    return last_word, string_without_last_word


def prompt_gpt4_errorlessly(prompt):
    ok = False
    while not ok:  # to avoid "ServiceUnavailableError: The server is overloaded or not ready yet."
        try:
            response = openai.ChatCompletion.create(
                        model="gpt-4-1106-preview",
                        messages=[
                                  {"role": "user", "content": prompt}
                                  ],
                        max_tokens = 200,
                        temperature = 0
                        )
            ok = True

        except Exception as ex:
            print("error", ex)
            print("too much request, sleep for 5 seconds")
            time.sleep(5)

    return response["choices"][0]["message"]["content"]

conversations, utterances, labels = load_data_afd()
annotations = collections.defaultdict(list)

prior_conversation = ''

try:
    for i, (conv) in enumerate(utterances):
        print('INDEX: ', i)
        annotations_ci = []

        ### participant
        for utterance in conv.split('\n\n'):
            if utterance == '' or len(utterance) == ',':
                pass
            else:
                if len(conversations[i].split(utterance)) <= 1:
                    raise 'utterance not found in the corresponding conversation'

                conv_hist = conversations[i].split(utterance)[0]
                try:
                    speaker_id, conv_hist_v2 = extract_and_remove_last_word(conv_hist)
                    formatted_prompt = prompt.format(utterance=speaker_id + '\n' + utterance, conv_history=conv_hist_v2)
                    response_text = prompt_gpt4_errorlessly(formatted_prompt)
                    annotations_ci.append(response_text)
                    
                except Exception as e: # happens for one instance 
                    print('Error: ', e)
                    pass
                    

        annotations['data'].append(annotations_ci)

        if (i) % 100 == 0 and i!=0:
            with open(f'afd_dispute_tactics_annotations_0-{i}.jsonl', 'w') as f: # afd/oum/wikitac
                for key, value in annotations.items():
                    json.dump({key: value}, f)
                    f.write('\n')

    with open(f'adf_dispute_tactics_annotations_0-{i}.jsonl', 'w') as f:
        for key, value in annotations.items():
            json.dump({key: value}, f)
            f.write('\n')

except Exception as e:
    print(e)
    time.sleep(5)

INDEX:  0



 Given the following two sets of textual features for disagreement levels and non-disagreement labels:


Disagreement Levels:

Level 0: Name calling/hostility - Direct insults, or use of an equally hostile tone or language.

Level 1: Ad hominem/ad argument - An attack to the person, often used to attempt to discredit an opponent (e.g., "I know better than you; you do not have a physics degree"). This category was extended to include "ad argument", where someone insults another's argument (e.g., "that is ridiculous") without responding to its content.

Level 2: Attempted derailing/off-topic - This category was added to address comments which are unrelated to the current line of discussion and fail to further the argument, while still being argumentative. This category is also represented in the Talk page taxonomy of Viegas et al. (2007). It was assigned a lower level as it can be detrimental to the argument, by taking focus away from the main topic.

Level 3: Policing the d

# 4 Post-process the outputs from GPT-4 for the annnotations of dispute tactics
The codes below is applied for AFD but can be easily adapted to oum or wikitactics by simply reading the corresponding JSONL data file

In [1]:
import re
import csv
import json
import pandas as pd

def clean_response(response):
    response = response.replace('[', '').replace(']', '')
    pattern = r"- Level \d: (\d)\n|- Label [A-I]: (\d)"
    matches = re.findall(pattern, response)
    
    cleaned_response = {}

    for match in matches:
        if match[0]:
            level = f"Level {len(cleaned_response)}"
            cleaned_response[level] = int(match[0])
        else:
            label = f"Label {chr(ord('A') + len(cleaned_response) - 8)}"
            cleaned_response[label] = int(match[1])

    return cleaned_response

# Load the JSONL data
data = {}
with open('afd_dispute_tactics_annotations_0-999.jsonl') as f:
    for line in f:
        json_data = json.loads(line)
        for key, value in json_data.items():
            data.setdefault(key, []).extend(value)

# Clean the responses and convert to CSV format
csv_data = []
header = ['Entity', 'Conversation', 'Response', 'Level 0', 'Level 1', 'Level 2', 'Level 3', 'Level 4', 'Level 5', 'Level 6', 'Level 7',
          'Label A', 'Label B', 'Label C', 'Label D', 'Label E', 'Label F', 'Label G', 'Label H', 'Label I']
csv_data.append(header)

for key, conversations in data.items():
    for conv_idx, conversation in enumerate(conversations, start=1):
        for resp_idx, response in enumerate(conversation, start=1):
            cleaned_response = clean_response(response)
            row = [key, f"Conversation_{conv_idx}", f"Response_{resp_idx}"]  

            for level in range(8):
                row.append(cleaned_response.get(f"Level {level}", 0))

            for label in 'ABCDEFGHI':
                row.append(cleaned_response.get(f"Label {label}", 0))

            csv_data.append(row)

# Save the cleaned data to a CSV file
with open('1000_afd_dispute_tactics_gpt4.csv', 'w', newline='') as f:
    writer = csv.writer(f)
    writer.writerows(csv_data)

0                  1           2        3        4        5   \
0     Entity       Conversation    Response  Level 0  Level 1  Level 2   
1       data     Conversation_1  Response_1        0        0        0   
2       data     Conversation_1  Response_2        0        0        0   
3       data     Conversation_1  Response_3        0        0        0   
4       data     Conversation_2  Response_1        0        0        0   
...      ...                ...         ...      ...      ...      ...   
8493    data   Conversation_999  Response_4        0        0        0   
8494    data   Conversation_999  Response_5        0        0        0   
8495    data  Conversation_1000  Response_1        0        0        0   
8496    data  Conversation_1000  Response_2        0        0        0   
8497    data  Conversation_1000  Response_3        0        0        0   

           6        7        8        9        10       11       12       13  \
0     Level 3  Level 4  Level 5  Level 6  Level 7  Label A  Label B  Label C   
1           0        0        0        0        0        0        1        0   
2           0        1        0        0        0        0        0        0   
3           0        1        0        0        0        0        0        0   
4           0        1        0        0        0        0        1        0   
...       ...      ...      ...      ...      ...      ...      ...      ...   
8493        0        1        0        0        0        0        0        0   
8494        0        1        0        0        0        0        0        0   
8495        0        1        0        0        0        0        1        0   
8496        0        1        0        0        0        0        0        0   
8497        0        1        0        0        0        0        0        0   

           14       15       16       17       18       19  
0     Label D  Label E  Label F  Label G  Label H  Label I  
1           0        0        0        0        0        0  
2           0        0        0        0        0        0  
3           0        0        0        0        0        0  
4           0        0        0        0        0        0  
...       ...      ...      ...      ...      ...      ...  
8493        0        0        0        0        0        0  
8494        1        0        0        0        0        0  
8495        0        0        0        0        0        0  
8496        0        0        0        0        0        0  
8497        0        0        0        0        0        0  

[8498 rows x 20 columns]

# 5. Obtain the mean and grad

In [ ]:
import pandas as pd
import numpy as np
from collections import defaultdict

# Read the data from the document_content
data = pd.read_csv('1000_afd_dispute_tactics_gpt4.csv')

# Get unique conversations
conversations = data['Conversation'].unique()

# Define the features (levels and labels)
features = ['Level 0', 'Level 1', 'Level 2', 'Level 3', 'Level 4', 'Level 5', 'Level 6', 'Level 7',
            'Label A', 'Label B', 'Label C', 'Label D', 'Label E', 'Label F', 'Label G', 'Label H', 'Label I']

# Initialize dictionaries to store the mean and gradient values
mean_values = defaultdict(list)
grad_values = defaultdict(list)

# Iterate over each conversation
for i, conversation in enumerate(conversations):
    
    # Iterate over each feature
    for feature in features:
        # Calculate the mean for participant data
        feature_values = data[data['Conversation']==conversation][feature].tolist()
        mean_values[feature].append(np.mean(feature_values))

        # Calculate the gradient for participant data
        x = np.arange(len(feature_values))
        y = feature_values
        try:
            slope, _ = np.polyfit(x, y, 1)
        except:
            slope = 0
        grad_values[feature].append(slope)


# Create DataFrames for participant and non-participant data
df_mean = pd.DataFrame(mean_values, index=conversations).add_suffix('_mean')
df_grad = pd.DataFrame(grad_values, index=conversations).add_suffix('_grad')

# Concatenate the DataFrames
result_df = pd.concat([df_mean, df_grad], axis=1)

# Reset the index and rename the 'Conversation' column
result_df.reset_index(inplace=True)
result_df.rename(columns={'index': 'Conversation'}, inplace=True)

# Save the result as a CSV file
del result_df['Conversation']
result_df.columns = ['DT-' + c for c in result_df.columns]
result_df.to_csv('1000_afd_gpt4_dispute_tactics.csv', index=False)